In [1]:
import qmpy_rester as qr

In [2]:
def structure_inspection(structure):
    """
    Need to know the coordination in a given oxide, the 2.5 Å cutoff could be tuned per element
    """
    num_o_sites = 0 
    m_coordinations = []
    for site in structure.sites:
        if str(site.specie)=='O':
            num_o_sites += 1
        else:
            # check nearest neighbours for coordination
            nn_info = structure.get_neighbors(site, 2.5)
            m_coord = 0
            for nn in nn_info:
                #print(str(nn.specie))
                if str(nn.specie)=="O":
                    m_coord+=1
                #assert str(nn.specie)=='O'
            m_coordinations.append(m_coord)
    o_percent = num_o_sites/len(structure.sites)
    ox_state = round((o_percent*2/(1-o_percent)), 3)
    return m_coordinations, ox_state

In [3]:
# Import libraries

import requests
from copy import deepcopy
import os
import shutil
import json

In [4]:
# Set the base URL for OPTIMADE REST queries

rest_base = "http://oqmd.org/optimade/structures?"

In [5]:
elements2consider = [ "Ti", "V", "Cr", "Mn", "Fe", "Co", "Ni", "Cu", "Nb", "Mo",
           "Li", "Be", "Na", "Mg", "K", "Ca", "Rb", "Sr", "Cs", "Ba",
            "Sc", "Ti", "V", "Cr", "Mn", "Fe", "Co", "Ni", "Cu", "Zn",
            "Ga", "Ge", "As", "Se", "Br",
            "Y", "Zr", "Nb", "Mo", "Tc", "Ru", "Rh", "Pd", "Ag", "Cd",
            "In", "Sn", "Sb", "Te", "I",
            "Hf", "Ta", "W", "Re", "Os", "Ir", "Pt", "Au", "Hg", 
            "Tl", "Pb", "Bi",
           "La", "Ce", "Nd", "Pr", "Sm", "Eu", "Gd", "Tb", "Dy", "Ho", "Er", "Tm", "Yb", "Lu"]

# Create the query URL with filter, response_fields and paging requirements

# The following query filters for data of ternary non-metallic oxides
# Crystal structure parameters and Band gap values are returned in response_fields
# Crystal structures will be used to generate representational vectors (input features) for ML
# Bandgap values will be used as targets for ML
oqmd_optimade_queries = []
for ele in elements2consider:

    # filter_   = 'stability<=0 AND elements HAS "O" AND elements HAS "Sn" AND nelements<3'
    # response_ = 'id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap'
    filter_   = 'elements HAS "O" AND elements HAS "{}" AND nelements<3 AND nelements>1'.format(ele)
    response_ = 'id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability'

    page_     = ["page_offset=0", 
                 "page_limit=200"]

    filter_   = 'filter=' + filter_
    response_ = 'response_fields=' + response_
    oqmd_optimade_queries.append(rest_base + "&".join([filter_, response_]+page_))
    print("Created Query: \n\n{}".format(oqmd_optimade_queries[-1]))

Created Query: 

http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Ti" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
Created Query: 

http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "V" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
Created Query: 

http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Cr" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
Created Query: 

http://oqmd.org/optimade/structures?filter

In [6]:
response = requests.get(oqmd_optimade_queries[0])
if response.status_code == 200:
    print("Success!")
    #print(response.json())
else:
    print("Query failed. Status: {}".format(response.status_code))
    print("Error Message: {}".format(response.text))

Success!


In [7]:
# We need more than 200 datapoints for machine learning - if more data is available

# As the first step, here's the same script from the cell above, but kept inside a function 

def query_oqmd_optimade(query):
    print("\nQuerying: {}".format(query))
    print(query)
    response = requests.get(query)
    if response.status_code == 200:
        print("Success!")
        return response.json()
    else:
        print("Query failed. Status: {}".format(response.status_code))
        print("Error Message: {}".format(response.text))
        return 

    
    

# Next, we query for 1000 materials in total using 5 sequential API queries - each paginated to
# retrieve 200 materials


load_data_from_saved = False  
# This is to avoid querying OQMD repeatedly for the same data, if .
# Because the data I downloaded is already available as a JSON file in this Git repo.

# But if you'd like to try out querying OQMD, set "load_data_from_saved" as "False"
# Querying OQMD for this particular data would take about 5-10 minutes to complete

datasets = []
for idx, oqmd_optimade_query in enumerate(oqmd_optimade_queries):
    dataset = []
    query = oqmd_optimade_query
    #oqmd_optimade_query
    for i in range(5):
        jsondata = query_oqmd_optimade(oqmd_optimade_query)
        if jsondata is None:
            break
        else:
            # Get the link to the next page and query it in next loop iteration
            query = deepcopy(jsondata['links']['next'])
            dataset.append(deepcopy(jsondata))
    
    filename = 'oqmd_data/json_data/{}_data.json'.format(elements2consider[idx])
    with open(filename, 'w') as fout:
        json.dump(dataset, fout)
    datasets.append(dataset)


Querying: http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Ti" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Ti" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
Success!

Querying: http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Ti" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "

Success!

Querying: http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Cr" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Cr" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
Success!

Querying: http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Mn" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
http://oqmd.org/optimade/structures?filter=elements HAS "O" AND eleme

Success!

Querying: http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Co" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Co" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
Success!

Querying: http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Co" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
http://oqmd.org/optimade/structures?filter=elements HAS "O" AND eleme

Success!

Querying: http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Nb" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Nb" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
Success!

Querying: http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Nb" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
http://oqmd.org/optimade/structures?filter=elements HAS "O" AND eleme

Success!

Querying: http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Be" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Be" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
Success!

Querying: http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Be" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
http://oqmd.org/optimade/structures?filter=elements HAS "O" AND eleme

...

Success!

Querying: http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Nd" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Nd" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
Success!

Querying: http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Nd" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
http://oqmd.org/optimade/structures?filter=elements HAS "O" AND eleme

Success!

Querying: http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Eu" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Eu" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
Success!

Querying: http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Eu" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
http://oqmd.org/optimade/structures?filter=elements HAS "O" AND eleme

Success!

Querying: http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Dy" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Dy" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
Success!

Querying: http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Dy" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
http://oqmd.org/optimade/structures?filter=elements HAS "O" AND eleme

Success!

Querying: http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Er" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Er" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
Success!

Querying: http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Tm" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
http://oqmd.org/optimade/structures?filter=elements HAS "O" AND eleme

Success!

Querying: http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Lu" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Lu" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
Success!

Querying: http://oqmd.org/optimade/structures?filter=elements HAS "O" AND elements HAS "Lu" AND nelements<3 AND nelements>1&response_fields=id,_oqmd_entry_id,lattice_vectors,cartesian_site_positions,species_at_sites,_oqmd_band_gap,_oqmd_spacegroup,_oqmd_delta_e,_oqmd_stability&page_offset=0&page_limit=200
http://oqmd.org/optimade/structures?filter=elements HAS "O" AND eleme

In [8]:
datasets[-1]

[{'links': {'next': None,
   'previous': None,
   'base_url': {'href': 'https://oqmd.org/optimade',
    'meta': {'_oqmd_version': '1.0'}}},
  'resource': {},
  'data': [{'id': 4477608,
    'type': 'structures',
    'attributes': {'lattice_vectors': [[2.860006, 0.0, 0.0],
      [0.0, 2.860006, 0.0],
      [0.0, 0.0, 2.860006]],
     'species_at_sites': ['Lu', 'O'],
     'cartesian_site_positions': [[0.0, 0.0, 0.0], [1.43, 1.43, 1.43]],
     '_oqmd_entry_id': 306645,
     '_oqmd_band_gap': 0.0,
     '_oqmd_delta_e': -2.2501,
     '_oqmd_stability': 1.051,
     '_oqmd_spacegroup': 'Pm-3m'}},
   {'id': 4515384,
    'type': 'structures',
    'attributes': {'lattice_vectors': [[2.025298, 2.025298, 0.0],
      [0.0, 4.050595, 0.0],
      [0.0, 0.0, 2.873368]],
     'species_at_sites': ['Lu', 'O'],
     'cartesian_site_positions': [[0.0, 0.0, 0.0], [0.0, 2.0253, 1.43669]],
     '_oqmd_entry_id': 338187,
     '_oqmd_band_gap': 0.0,
     '_oqmd_delta_e': -1.9886,
     '_oqmd_stability': 1.313,
 

In [9]:
# Here's a function to convert OPTIMADE's structure data to POSCAR. 

# Make sure that 'lattice_vectors', 'species_at_sites', and 'cartesian_site_positions' are
# included in the response_fields of query URL

def get_poscar_from_optimade_structure(structure):
    if '_oqmd_entry_id' in structure['attributes'].keys():
        poscar =  ["REST API StructureID {}, OQMD Entry ID {}".format(
            structure['id'], structure['attributes']['_oqmd_entry_id']
        )]
        filename = "ID-{}_OQMD-EnID-{}.poscar".format(structure['id'],structure['attributes']['_oqmd_entry_id'])
    else:
        poscar =  ["REST API StructureID {}".format(structure['id'])]
        filename = "ID-{}.poscar".format(structure['id'])
        
    poscar.append("1.0")
    
    poscar += [" ".join([str(jtem) for jtem in item]) 
               for item in structure['attributes']['lattice_vectors']
              ]
    
    elems  = []
    counts = []
    for item in structure['attributes']['species_at_sites']:
        if item in elems:
            assert elems.index(item) == len(elems)-1
            counts[-1] += 1
        else:
            elems.append(deepcopy(item))
            counts.append(1)
    poscar.append(" ".join(elems))
    poscar.append(" ".join([str(item) for item in counts]))
    
    poscar.append("Cartesian")
    
    poscar += [" ".join([str(jtem) for jtem in item]) 
               for item in structure['attributes']['cartesian_site_positions']
              ]
    poscar = "\n".join(poscar)
    return (poscar, filename)

In [10]:
datasets[0][0]['data']

[{'id': 4061754,
  'type': 'structures',
  'attributes': {'lattice_vectors': [[2.125829, -2.125829, 0.0],
    [-2.125829, 0.0, -2.125829],
    [2.125829, 2.125829, 0.0]],
   'species_at_sites': ['O', 'Ti'],
   'cartesian_site_positions': [[2.12583, 0.0, 0.0], [0.0, 0.0, 0.0]],
   '_oqmd_entry_id': 17898,
   '_oqmd_band_gap': 0.0,
   '_oqmd_delta_e': -2.5223,
   '_oqmd_stability': 0.22,
   '_oqmd_spacegroup': 'Fm-3m'}},
 {'id': 4089960,
  'type': 'structures',
  'attributes': {'lattice_vectors': [[0.0, 0.0, -4.145527],
    [-1.393558, 4.42519, 2.072763],
    [5.812852, 0.003849, 0.0]],
   'species_at_sites': ['O', 'O', 'O', 'O', 'O', 'Ti', 'Ti', 'Ti', 'Ti', 'Ti'],
   'cartesian_site_positions': [[0.0, 0.0, -2.07276],
    [0.06309, 2.89953, -2.07276],
    [1.51351, 1.51076, -0.0],
    [2.90578, 2.91828, -2.07276],
    [4.3562, 1.52951, -0.0],
    [0.07204, 3.00063, -0.0],
    [1.48902, 1.31989, -2.07276],
    [1.51287, 4.42711, -2.07276],
    [2.93028, 3.10915, 0.0],
    [4.34725, 1.4284

In [11]:
for idx, ele in enumerate(elements2consider):
    #print(ele)
    if ele=='Si':
        continue
    # Call the OPTIMADE structure -> POSCAR conversion function 
    # and save all structures in directory "./input_poscars"

    # Also save the bandgap values in a file "target_properties.csv"

    poscar_dir = "oqmd_data/input_poscars/input_poscars_{}o2".format(ele)
    if os.path.exists(poscar_dir):
        shutil.rmtree(poscar_dir)
    os.mkdir(poscar_dir)

    properties = []

    for dt in datasets[idx]:
        for st in dt['data']:
            print(st)
            poscar, filename = get_poscar_from_optimade_structure(deepcopy(st))
            target_value = deepcopy(st['attributes']['_oqmd_delta_e'])
            spg = deepcopy(st['attributes']['_oqmd_spacegroup'])
            properties.append(",".join([filename,str(target_value), str(spg)]))
            with open(os.path.join(poscar_dir,filename),"w") as fout:
                fout.write(poscar)
    with open("oqmd_data/target_props/target_properties_{}o2.csv".format(ele),"w") as fout:
        fout.write("filename, _oqmd_delta_e, _oqmd_spacegroup \n")
        fout.write("\n".join(properties))

{'id': 4061754, 'type': 'structures', 'attributes': {'lattice_vectors': [[2.125829, -2.125829, 0.0], [-2.125829, 0.0, -2.125829], [2.125829, 2.125829, 0.0]], 'species_at_sites': ['O', 'Ti'], 'cartesian_site_positions': [[2.12583, 0.0, 0.0], [0.0, 0.0, 0.0]], '_oqmd_entry_id': 17898, '_oqmd_band_gap': 0.0, '_oqmd_delta_e': -2.5223, '_oqmd_stability': 0.22, '_oqmd_spacegroup': 'Fm-3m'}}
{'id': 4089960, 'type': 'structures', 'attributes': {'lattice_vectors': [[0.0, 0.0, -4.145527], [-1.393558, 4.42519, 2.072763], [5.812852, 0.003849, 0.0]], 'species_at_sites': ['O', 'O', 'O', 'O', 'O', 'Ti', 'Ti', 'Ti', 'Ti', 'Ti'], 'cartesian_site_positions': [[0.0, 0.0, -2.07276], [0.06309, 2.89953, -2.07276], [1.51351, 1.51076, -0.0], [2.90578, 2.91828, -2.07276], [4.3562, 1.52951, -0.0], [0.07204, 3.00063, -0.0], [1.48902, 1.31989, -2.07276], [1.51287, 4.42711, -2.07276], [2.93028, 3.10915, 0.0], [4.34725, 1.42841, -2.07276]], '_oqmd_entry_id': 10207, '_oqmd_band_gap': 0.0, '_oqmd_delta_e': -2.7428, '

{'id': 5812783, 'type': 'structures', 'attributes': {'lattice_vectors': [[3.276338506, 0.0, 0.0], [-1.638169253, 2.837392378, 0.0], [0.0, 0.0, 5.335146394]], 'species_at_sites': ['O', 'O', 'O', 'V', 'V'], 'cartesian_site_positions': [[0.0, 0.0, 0.0], [1.63817, 0.9458, 1.90754], [-0.0, 1.89159, 3.42761], [-0.0, 1.89159, 1.30508], [1.63817, 0.9458, 4.03007]], '_oqmd_entry_id': 1440426, '_oqmd_band_gap': 1.488, '_oqmd_delta_e': -2.494, '_oqmd_stability': 0.137, '_oqmd_spacegroup': 'P-3m1'}}
{'id': 5816138, 'type': 'structures', 'attributes': {'lattice_vectors': [[5.639396814, -1.520131402, 0.0], [5.639396814, 1.520131402, 0.0], [-1.888396519, 0.0, 6.208260195]], 'species_at_sites': ['O', 'O', 'O', 'O', 'O', 'O', 'V', 'V', 'V', 'V'], 'cartesian_site_positions': [[1.69904, 0.0, 0.17651], [5.36544, 0.0, 1.82283], [8.24381, 0.0, 2.22246], [1.14659, 0.0, 3.9858], [4.02495, 0.0, 4.38543], [7.69136, 0.0, 6.03175], [3.59684, 0.0, 1.08196], [0.92778, 0.0, 2.00042], [8.46261, 0.0, 4.20785], [5.7935

{'id': 4468686, 'type': 'structures', 'attributes': {'lattice_vectors': [[2.758337, 0.0, 0.0], [0.0, 2.758337, 0.0], [0.0, 0.0, 2.758337]], 'species_at_sites': ['Mn', 'O'], 'cartesian_site_positions': [[0.0, 0.0, 0.0], [1.37917, 1.37917, 1.37917]], '_oqmd_entry_id': 305726, '_oqmd_band_gap': 0.426, '_oqmd_delta_e': -1.4915, '_oqmd_stability': 0.547, '_oqmd_spacegroup': 'Pm-3m'}}
{'id': 4500522, 'type': 'structures', 'attributes': {'lattice_vectors': [[1.573927, 0.908707, 2.592709], [-1.573927, 0.908707, 2.592709], [0.0, -1.817413, 2.592709]], 'species_at_sites': ['Mn', 'O'], 'cartesian_site_positions': [[0.0, 0.0, 0.0], [0.0, 0.0, 3.88907]], '_oqmd_entry_id': 326810, '_oqmd_band_gap': 0.423, '_oqmd_delta_e': -2.0367, '_oqmd_stability': 0.001, '_oqmd_spacegroup': 'R-3m'}}
{'id': 4512804, 'type': 'structures', 'attributes': {'lattice_vectors': [[1.946693, 1.946693, 0.0], [0.0, 3.893388, 0.0], [0.0, 0.0, 2.754311]], 'species_at_sites': ['Mn', 'O'], 'cartesian_site_positions': [[0.0, 0.0, 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



{'id': 5813507, 'type': 'structures', 'attributes': {'lattice_vectors': [[3.185268144, 0.0, 0.0], [-1.592634072, 2.758523131, 0.0], [0.0, 0.0, 8.154219314]], 'species_at_sites': ['O', 'O', 'O', 'O', 'Re', 'Re'], 'cartesian_site_positions': [[0.0, 0.0, 0.91489], [0.0, 1.83902, 3.15995], [0.0, 0.0, 4.992], [1.59263, 0.91951, 7.23706], [0.0, 1.83902, 0.00269], [1.59263, 0.91951, 4.0798]], '_oqmd_entry_id': 1442557, '_oqmd_band_gap': 0.0, '_oqmd_delta_e': -1.1469, '_oqmd_stability': 0.561, '_oqmd_spacegroup': 'P63mc'}}
{'id': 5813707, 'type': 'structures', 'attributes': {'lattice_vectors': [[4.316855289, 0.0, 0.0], [0.0, 4.316855289, 0.0], [0.0, 0.0, 4.316855289]], 'species_at_sites': ['O', 'O', 'O', 'O', 'Re', 'Re'], 'cartesian_site_positions': [[1.07921, 1.07921, 1.07921], [3.23764, 3.23764, 1.07921], [3.23764, 1.07921, 3.23764], [1.07921, 3.23764, 3.23764], [0.0, 0.0, 0.0], [2.15843, 2.15843, 2.15843]], '_oqmd_entry_id': 1442800, '_oqmd_band_gap': 0.0, '_oqmd_delta_e': -1.0525, '_oqmd_s

{'id': 4120953, 'type': 'structures', 'attributes': {'lattice_vectors': [[-1.522262, 1.522262, 4.743771], [1.522262, -1.522262, 4.743771], [1.522262, 1.522262, -4.743771]], 'species_at_sites': ['Hg', 'O', 'O', 'O'], 'cartesian_site_positions': [[0.0, 0.0, 0.0], [0.0, 1.52226, 2.37189], [1.52226, 0.0, 2.37189], [0.0, 0.0, 4.74377]], '_oqmd_entry_id': 302755, '_oqmd_band_gap': 0.0, '_oqmd_delta_e': 0.7962, '_oqmd_stability': 1.026, '_oqmd_spacegroup': 'I4/mmm'}}
{'id': 4140969, 'type': 'structures', 'attributes': {'lattice_vectors': [[0.0, 2.750849, 2.750849], [2.750849, 0.0, 2.750849], [2.750849, 2.750849, 0.0]], 'species_at_sites': ['Hg', 'O', 'O', 'O'], 'cartesian_site_positions': [[4.12627, 4.12627, 4.12627], [0.0, 0.0, 0.0], [2.75085, 2.75085, 2.75085], [1.37542, 1.37542, 1.37542]], '_oqmd_entry_id': 313297, '_oqmd_band_gap': 0.0, '_oqmd_delta_e': 0.9079, '_oqmd_stability': 1.138, '_oqmd_spacegroup': 'Fm-3m'}}
{'id': 4148757, 'type': 'structures', 'attributes': {'lattice_vectors': [

{'id': 4092903, 'type': 'structures', 'attributes': {'lattice_vectors': [[3.911777, -7.5e-05, 3.7e-05], [-1.955953, 3.38781, 0.0], [5.7e-05, 3.3e-05, 6.10171]], 'species_at_sites': ['La', 'La', 'O', 'O', 'O'], 'cartesian_site_positions': [[0.00013, 2.25862, 1.50286], [1.95575, 1.12915, 4.59889], [0.0, 0.0, 0.0], [1.95574, 1.12915, 2.15809], [0.00014, 2.25862, 3.94366]], '_oqmd_entry_id': 10228, '_oqmd_band_gap': 3.938, '_oqmd_delta_e': -3.6877, '_oqmd_stability': 0.025, '_oqmd_spacegroup': 'P-3m1'}}
{'id': 4298886, 'type': 'structures', 'attributes': {'lattice_vectors': [[4.591663, 0.0, 0.0], [0.0, 4.591663, 0.0], [0.0, 0.0, 4.591663]], 'species_at_sites': ['La', 'La', 'O', 'O', 'O'], 'cartesian_site_positions': [[0.0, 0.0, 0.0], [2.29583, 2.29583, 2.29583], [2.29583, 2.29583, 0.0], [2.29583, 0.0, 2.29583], [0.0, 2.29583, 2.29583]], '_oqmd_entry_id': 351063, '_oqmd_band_gap': 0.595, '_oqmd_delta_e': -2.8246, '_oqmd_stability': 0.888, '_oqmd_spacegroup': 'Pm-3m'}}
{'id': 4509024, 'type'

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

